In [1]:
!pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 4.4 MB 8.1 MB/s 
     |████████████████████████████████| 596 kB 68.1 MB/s 
     |████████████████████████████████| 6.6 MB 71.7 MB/s 
     |████████████████████████████████| 101 kB 13.1 MB/s 
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13


In [2]:
import numpy as np
import pandas as pd
import random
import tensorflow as tf
import re
# import lineflow as lf
import IPython
import graphviz
import datetime
import os
import ast
import torch

from sklearn.metrics import accuracy_score
from tensorflow.keras.callbacks import EarlyStopping, TensorBoard, LearningRateScheduler
from tensorflow.keras.utils import plot_model
from tensorflow.keras.layers import Input, Dense, Dropout
from tensorflow.keras import Model

In [3]:
resolver = tf.distribute.cluster_resolver.TPUClusterResolver()
tf.config.experimental_connect_to_cluster(resolver)
# This is the TPU initialization code that has to be at the beginning.
tf.tpu.experimental.initialize_tpu_system(resolver)
print("All devices: ", tf.config.list_logical_devices('TPU'))

INFO:tensorflow:Deallocate tpu buffers before initializing tpu system.


INFO:tensorflow:Deallocate tpu buffers before initializing tpu system.


INFO:tensorflow:Initializing the TPU system: grpc://10.102.181.26:8470


INFO:tensorflow:Initializing the TPU system: grpc://10.102.181.26:8470


INFO:tensorflow:Finished initializing TPU system.


INFO:tensorflow:Finished initializing TPU system.


All devices:  [LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:0', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:1', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:2', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:3', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:4', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:5', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:6', device_type='TPU'), LogicalDevice(name='/job:worker/replica:0/task:0/device:TPU:7', device_type='TPU')]


In [57]:
df_easy_train = pd.read_csv('df_easy_train_2.csv')
df_easy_dev = pd.read_csv('df_easy_dev_2.csv')
df_easy_test = pd.read_csv('df_easy_test_2.csv')

In [58]:
df_easy_train.head()

AnswerKey                                           question  \
0         B  Which factor will most likely cause a person t...   
1         B  Lichens are symbiotic organisms made of green ...   
2         D  When a switch is used in an electrical circuit...   
3         A  Which of the following is an example of an ass...   
4         3  Rocks are classified as igneous, metamorphic, ...   

                                       only_question  \
0  Which factor will most likely cause a person t...   
1  Lichens are symbiotic organisms made of green ...   
2  When a switch is used in an electrical circuit...   
3  Which of the following is an example of an ass...   
4  Rocks are classified as igneous, metamorphic, ...   

                                        only_answers  quesiton_length  \
0  (A)  a leg muscle relaxing after exercise (B) ...               66   
1  (A)  carbon dioxide (B) food (C) protection (D...              139   
2  (A)  cause the charge to build. (B) increase a...               63   
3  (A)  contact lens (B) motorcycle (C) raincoat ...               61   
4  (1)  their color (2) their shape (3) how they ...               74   

                                        options_list  \
0  ['a leg muscle relaxing after exercise ', 'bac...   
1  ['carbon dioxide ', 'food ', 'protection ', 'w...   
2  ['cause the charge to build. ', 'increase and ...   
3  ['contact lens ', 'motorcycle ', 'raincoat ', ...   
4  ['their color ', 'shape ', 'how they formed ',...   

                                       option_1_docs  \
0  ['Which will most likely cause variations to o...   
1  ['Lichens are comprised of blue-green or green...   
2  ['When A Switch Is Closed In An Electrical Cir...   
3  ['Which of the following is an example of an a...   
4  ['Metamorphic rocks can begin as igneous, sedi...   

                                       option_2_docs  \
0  ['If a bacterial infection is the suspected ca...   
1  ['Lichens are comprised of blue-green or green...   
2  ['When A Switch Is Closed In An Electrical Cir...   
3  ['Which of the following is an example of an a...   
4  ['Metamorphic rocks can begin as igneous, sedi...   

                                       option_3_docs  \
0  ['A person who has been sick for one week with...   
1  ['Lichens are comprised of blue-green or green...   
2  ['When A Switch Is Closed In An Electrical Cir...   
3  ['Which of the following is an example of an a...   
4  ['Rocks are formed on Earth as igneous, sedime...   

                                       option_4_docs  \
0  ['Which will most likely cause variations to o...   
1  ['Lichens are comprised of blue-green or green...   
2  ['When A Switch Is Closed In An Electrical Cir...   
3  ['Which of the following is an example of an a...   
4  ['Metamorphic rocks can begin as igneous, sedi...   

                                       option_5_docs  \
0  ['Fever: most infections of the lung will caus...   
1  ['Lichens are comprised of blue-green or green...   
2  ['When A Switch Is Closed In An Electrical Cir...   
3  ['Which of the following is an example of an a...   
4  ['Metamorphic rocks can begin as igneous, sedi...   

                                             context  
0  If a bacterial infection is the suspected caus...  
1  Lichens are comprised of blue green or green a...  
2  VOLTAGE That force which is generated to cause...  
3  Which of the following is an example of an ang...  
4  Igneous sedimentary and metamorphic rocks how ...

In [97]:
df_challenge_train = pd.read_csv('df_challenge_train_2.csv')
df_challenge_dev = pd.read_csv('df_challenge_dev_2.csv')
df_challenge_test = pd.read_csv('df_challenge_test_2.csv')

In [98]:
df_challenge_train.head()

AnswerKey                                           question  \
0         A  George wants to warm his hands quickly by rubb...   
1         B  Which of the following statements best explain...   
2         B  A fold observed in layers of sedimentary rock ...   
3         D  Which of these do scientists offer as the most...   
4         B  A boat is acted on by a river current flowing ...   

                                       only_question  \
0  George wants to warm his hands quickly by rubb...   
1  Which of the following statements best explain...   
2  A fold observed in layers of sedimentary rock ...   
3  Which of these do scientists offer as the most...   
4  A boat is acted on by a river current flowing ...   

                                        only_answers  quesiton_length  \
0  (A)  dry palms (B) wet palms (C) palms covered...              103   
1  (A)  The refrigerator door is smooth. (B) The ...               98   
2  (A)  cooling of flowing magma. (B) converging ...               76   
3  (A)  worldwide disease (B) global mountain bui...              141   
4             (A)  west (B) east (C) north (D) south              198   

                                        options_list  \
0  ['dry palms ', 'wet ', 'covered with oil ', 'c...   
1  ['The refrigerator door is smooth. ', 'contain...   
2  ['cooling of flowing magma. ', 'converging cru...   
3  ['worldwide disease ', 'global mountain buildi...   
4  ['west ', 'east ', 'north ', 'south', 'None of...   

                                       option_1_docs  \
0  ['When the skin surface is exposed to heat, wa...   
1  ['Why does a magnet stick to a refrigerator do...   
2  ['Magma that intrudes between sedimentary rock...   
3  ['At the end of the Mesozoic Era\n', 'at the e...   
4  ['A windmill boat on a rapidly flowing river, ...   

                                       option_2_docs  \
0  ['When the skin surface is exposed to heat, wa...   
1  ['Which one of the following statements best e...   
2  ['sedimentary rock layers.\n', 'sedimentary ro...   
3  ['At the end of the Mesozoic Era\n', 'Many of ...   
4  ['A windmill boat on a rapidly flowing river, ...   

                                       option_3_docs  \
0  ['As a couple of taller kids hogged the ball, ...   
1  ['Which one of the following statements best e...   
2  ['Sedimentary Rock : A rock formed from layers...   
3  ['at the end of the Mesozoic Era\xa0 would hav...   
4  ['A windmill boat on a rapidly flowing river, ...   

                                       option_4_docs  \
0  ['As a couple of taller kids hogged the ball, ...   
1  ['Which one of the following statements best e...   
2  ['Sedimentary rock that forms when minerals cr...   
3  ['Most researchers agree that the Mesozoic Era...   
4  ['A windmill boat on a rapidly flowing river, ...   

                                       option_5_docs  \
0  ['As a couple of taller kids hogged the ball, ...   
1  ['Which one of the following statements best e...   
2  ['sedimentary rock layers.\n', 'sedimentary ro...   
3  ['At the end of the Mesozoic Era\n', 'at the e...   
4  ['A windmill boat on a rapidly flowing river, ...   

                                             context  
0  Most palms have skin Most hands have part palm...  
1  Why does a magnet stick to a refrigerator door...  
2  shale n a sedimentary rock formed by the depos...  
3  at the end of the Mesozoic Era would have seem...  
4  A windmill boat on a rapidly flowing river und...

In [99]:
def data_generator(a):
    '''
    This function will accept a data point and returns a list of options
    converts the only_options list of options.

    Output will be as follows:

    options = [option_1, option_2, option_3, option_4, option_5]                   

    Note: If there's no option E then it will be written as 'None of the above'.
    '''
    options = []

    if '(A)' in a:
        option_1 = a.split('(B)')[0].replace('(A)','').lstrip()

        b = ' '.join(i for i in a.split() if i not in option_1)
        option_2 = b.split('(C)')[0].replace('(B)','').replace('(A)','').lstrip()

        c = ' '.join(i for i in b.split() if i not in option_2)
        option_3 = c.split('(D)')[0].replace('(C)','').replace('(B)','').replace('(A)','').lstrip()

        if '(D)' not in c:
            option_4 = 'None of the above'
            option_5 = 'None of the above'
        else:
            if '(E)' not in c:
                option_4 = c.split('(D)')[1].lstrip()
                option_5 = 'None of the above'
            else:
                d = ' '.join(i for i in c.split() if i not in option_3)
                option_4 = d.split('(E)')[0].replace('(D)','').replace('(C)','').replace('(B)','').replace('(A)','').lstrip()
                option_5 = d.split('(E)')[1].lstrip()
    else:
        option_1 = a.split('(2)')[0].replace('(1)','').lstrip()

        b = ' '.join(i for i in a.split() if i not in option_1)
        option_2 = b.split('(3)')[0].replace('(2)','').replace('(1)','').lstrip()

        c = ' '.join(i for i in b.split() if i not in option_2)
        option_3 = c.split('(4)')[0].replace('(3)','').replace('(2)','').replace('(1)','').lstrip()

        if '(4)' in c:
            option_4 = c.split('(4)')[1].lstrip()
        else:
            option_4 = 'None of the above'
        option_5 = 'None of the above'

    options = [option_1, option_2, option_3, option_4, option_5]

    return options

In [62]:
df_easy_dev['options_list'] = df_easy_dev['only_answers'].map(data_generator)
df_easy_train['options_list'] = df_easy_train['only_answers'].map(data_generator)
df_easy_test['options_list'] = df_easy_test['only_answers'].map(data_generator)

In [100]:
df_challenge_dev['options_list'] = df_challenge_dev['only_answers'].map(data_generator)
df_challenge_train['options_list'] = df_challenge_train['only_answers'].map(data_generator)
df_challenge_test['options_list'] = df_challenge_test['only_answers'].map(data_generator)

In [102]:
def answer(answer_key, options_list):

    label_map = {'A':0,
             'B':1,
             'C':2,
             'D':3,
             'E':4,
             '1':0,
             '2':1,
             '3':2,
             '4':3,
             '5':4}
    
    number = label_map.get(answer_key)
    answer = options_list[number]
    return answer

In [64]:
df_easy_train['Answer'] = df_easy_train[['AnswerKey', 'options_list']].apply(lambda x: answer(*x), axis=1)
df_easy_dev['Answer'] = df_easy_dev[['AnswerKey', 'options_list']].apply(lambda x: answer(*x), axis=1)
df_easy_test['Answer'] = df_easy_test[['AnswerKey', 'options_list']].apply(lambda x: answer(*x), axis=1)

In [103]:
df_challenge_train['Answer'] = df_challenge_train[['AnswerKey', 'options_list']].apply(lambda x: answer(*x), axis=1)
df_challenge_dev['Answer'] = df_challenge_dev[['AnswerKey', 'options_list']].apply(lambda x: answer(*x), axis=1)
df_challenge_test['Answer'] = df_challenge_test[['AnswerKey', 'options_list']].apply(lambda x: answer(*x), axis=1)

In [104]:
label_map = {'A':0,
             'B':1,
             'C':2,
             'D':3,
             'E':4,
             '1':0,
             '2':1,
             '3':2,
             '4':3,
             '5':4}

easy_train_labels = df_easy_train['AnswerKey'].map(label_map)
easy_dev_labels = df_easy_dev['AnswerKey'].map(label_map)
easy_test_labels = df_easy_test['AnswerKey'].map(label_map)

In [67]:
np.save('easy_train_labels', easy_train_labels)
np.save('easy_dev_labels', easy_dev_labels)
np.save('easy_test_labels',easy_test_labels)

In [105]:
label_map = {'A':0,
             'B':1,
             'C':2,
             'D':3,
             'E':4,
             '1':0,
             '2':1,
             '3':2,
             '4':3,
             '5':4}

challenge_train_labels = df_challenge_train['AnswerKey'].map(label_map)
challenge_dev_labels = df_challenge_dev['AnswerKey'].map(label_map)
challenge_test_labels = df_challenge_test['AnswerKey'].map(label_map)

In [69]:
np.save('challenge_train_labels', challenge_train_labels)
np.save('challenge_dev_labels', challenge_dev_labels)
np.save('challenge_test_labels',challenge_test_labels)

## Baseline Model.

For base model we will select answers randomly.

In [ ]:
char_list_1 = ['A','B','C','D']
char_list_2 = ['A','B','C','D','E']
num_list = ['1','2','3','4']

In [ ]:
easy_train_preds = []
easy_dev_preds = []
easy_test_preds = []

for i in range(len(df_easy_train)):
    if '(1)' in df_easy_train['only_answers'].iloc[i]:
        easy_train_preds.append(random.choice(num_list))
    else:
        if '(E)' in df_easy_train['only_answers'].iloc[i]:
            easy_train_preds.append(random.choice(char_list_2))
        else:
            easy_train_preds.append(random.choice(char_list_1))

In [ ]:
for i in range(len(df_easy_dev)):
    if '(1)' in df_easy_dev['only_answers'].iloc[i]:
        easy_dev_preds.append(random.choice(num_list))
    else:
        if '(E)' in df_easy_dev['only_answers'].iloc[i]:
            easy_dev_preds.append(random.choice(char_list_2))
        else:
            easy_dev_preds.append(random.choice(char_list_1))

In [ ]:
for i in range(len(df_easy_test)):
    if '(1)' in df_easy_test['only_answers'].iloc[i]:
        easy_test_preds.append(random.choice(num_list))
    else:
        if '(E)' in df_easy_test['only_answers'].iloc[i]:
            easy_test_preds.append(random.choice(char_list_2))
        else:
            easy_test_preds.append(random.choice(char_list_1))

In [ ]:
challenge_train_preds = []
challenge_dev_preds = []
challenge_test_preds = []

for i in range(len(df_challenge_train)):
    if '(1)' in df_challenge_train['only_answers'].iloc[i]:
        challenge_train_preds.append(random.choice(num_list))
    else:
        if '(E)' in df_challenge_train['only_answers'].iloc[i]:
            challenge_train_preds.append(random.choice(char_list_2))
        else:
            challenge_train_preds.append(random.choice(char_list_1))

for i in range(len(df_challenge_dev)):
    if '(1)' in df_challenge_dev['only_answers'].iloc[i]:
        challenge_dev_preds.append(random.choice(num_list))
    else:
        if '(E)' in df_challenge_dev['only_answers'].iloc[i]:
            challenge_dev_preds.append(random.choice(char_list_2))
        else:
            challenge_dev_preds.append(random.choice(char_list_1))

for i in range(len(df_challenge_test)):
    if '(1)' in df_challenge_test['only_answers'].iloc[i]:
        challenge_test_preds.append(random.choice(num_list))
    else:
        if '(E)' in df_challenge_test['only_answers'].iloc[i]:
            challenge_test_preds.append(random.choice(char_list_2))
        else:
            challenge_test_preds.append(random.choice(char_list_1))

In [ ]:
easy_train_score = accuracy_score(df_easy_train['AnswerKey'], easy_train_preds)
easy_dev_score = accuracy_score(df_easy_dev['AnswerKey'], easy_dev_preds)
easy_test_score = accuracy_score(df_easy_test['AnswerKey'], easy_test_preds)

print(f'Accuracy score on easy train set is {easy_train_score}.')
print(f'Accuracy score on easy dev set is {easy_dev_score}.')
print(f'Accuracy score on easy test set is {easy_test_score}.')

Accuracy score on easy train set is 0.2543186180422265.
Accuracy score on easy dev set is 0.24561403508771928.
Accuracy score on easy test set is 0.2375366568914956.


In [ ]:
challenge_train_score = accuracy_score(df_challenge_train['AnswerKey'], challenge_train_preds)
challenge_dev_score = accuracy_score(df_challenge_dev['AnswerKey'], challenge_dev_preds)
challenge_test_score = accuracy_score(df_challenge_test['AnswerKey'], challenge_test_preds)

print(f'Accuracy score on challenge train set is {challenge_train_score}.')
print(f'Accuracy score on challenge dev set is {challenge_dev_score}.')
print(f'Accuracy score on challenge test set is {challenge_test_score}.')

Accuracy score on challenge train set is 0.24664879356568364.
Accuracy score on challenge dev set is 0.2909698996655518.
Accuracy score on challenge test set is 0.25341296928327645.


## BERT Model.

#### Preparing data according to BERT

In [ ]:
from transformers import BertTokenizer, TFBertForMultipleChoice

In [ ]:
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased', do_lower_case=True)

Downloading:   0%|          | 0.00/226k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/28.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/570 [00:00<?, ?B/s]

In [ ]:
MAX_LEN = 512

In [ ]:
def arc_preprocessor(dataset, tokenizer):
    '''
    This function will convert a given context, question, choices in a format:

    [CLS] context [SEP] question choices[0] [SEP]
    [CLS] context [SEP] question choices[1] [SEP]
    [CLS] context [SEP] question choices[2] [SEP]
    [CLS] context [SEP] question choices[3] [SEP]

    After converting in this format the data will be tokenized using a given tokenizer.
    This function will return 4 arrays namely, input_ids, attention_mask, token_type_ids and labels.

    individual input_ids, token_type_ids, attention_mask shape will be as: [num_choices, max_seq_length]
    '''
    all_input_ids = []
    all_attention_mask = []
    all_token_type_ids = []

    for i in range(len(dataset)):

        context = dataset['context'].iloc[i]
        question = dataset['only_question'].iloc[i]
        options = dataset['options_list'].iloc[i]
        choice_features = []

        for j in range(len(options)):

            option = options[j]
            ques_opt = question + ' ' + f'{j}' + ' ' + option
            ques_opt = re.sub(r'\s+', ' ', ques_opt)

            inputs = tokenizer(context,
                               ques_opt,
                               max_length=MAX_LEN,
                               truncation='only_first',
                               padding='max_length')
            
            input_ids = inputs['input_ids']
            attention_mask = inputs['attention_mask']
            token_type_ids = inputs['token_type_ids']

            assert len(input_ids) == MAX_LEN
            assert len(token_type_ids) == MAX_LEN
            assert len(attention_mask) == MAX_LEN

            choice_features.append({'input_ids':input_ids,
                                    'attention_mask':attention_mask,
                                    'token_type_ids':token_type_ids})

        all_input_ids.append(np.asarray([cf['input_ids'] for cf in choice_features], dtype='int32'))
        all_attention_mask.append(np.asarray([cf['attention_mask'] for cf in choice_features], dtype='int32'))
        all_token_type_ids.append(np.asarray([cf['token_type_ids'] for cf in choice_features], dtype='int32'))

    return all_input_ids, all_attention_mask, all_token_type_ids

In [ ]:
easy_train_input_ids, easy_train_attention_mask, easy_train_token_type_ids = arc_preprocessor(df_easy_train, tokenizer)
easy_dev_input_ids, easy_dev_attention_mask, easy_dev_token_type_ids = arc_preprocessor(df_easy_dev, tokenizer)
easy_test_input_ids, easy_test_attention_mask, easy_test_token_type_ids = arc_preprocessor(df_easy_test, tokenizer)

In [ ]:
easy_train_input_ids = np.asarray(easy_train_input_ids, dtype='int32')
easy_train_token_type_ids = np.asarray(easy_train_token_type_ids, dtype='int32')
easy_train_attention_mask = np.asarray(easy_train_attention_mask, dtype='int32')

In [ ]:
easy_dev_input_ids = np.asarray(easy_dev_input_ids, dtype='int32')
easy_dev_token_type_ids = np.asarray(easy_dev_token_type_ids, dtype='int32')
easy_dev_attention_mask = np.asarray(easy_dev_attention_mask, dtype='int32')

In [ ]:
easy_test_input_ids = np.asarray(easy_test_input_ids, dtype='int32')
easy_test_token_type_ids = np.asarray(easy_test_token_type_ids, dtype='int32')
easy_test_attention_mask = np.asarray(easy_test_attention_mask, dtype='int32')

In [ ]:
easy_train_input_ids.shape

(2251, 5, 512)

In [ ]:
np.save('easy_train_input_ids.npy', easy_train_input_ids)
np.save('easy_train_attention_mask.npy', easy_train_attention_mask)
np.save('easy_train_token_type_ids.npy', easy_train_token_type_ids)

In [ ]:
np.save('easy_dev_input_ids.npy', easy_dev_input_ids)
np.save('easy_dev_attention_mask.npy', easy_dev_attention_mask)
np.save('easy_dev_token_type_ids.npy', easy_dev_token_type_ids)

In [ ]:
np.save('easy_test_input_ids.npy', easy_test_input_ids)
np.save('easy_test_attention_mask.npy', easy_test_attention_mask)
np.save('easy_test_token_type_ids.npy', easy_test_token_type_ids)

## Training BERT

In [ ]:
easy_dev_input_ids = np.load('easy_dev_input_ids.npy')
easy_dev_attention_mask = np.load('easy_dev_attention_mask.npy')
easy_dev_token_type_ids = np.load('easy_dev_token_type_ids.npy')

In [ ]:
easy_test_input_ids = np.load('easy_test_input_ids.npy')
easy_test_attention_mask = np.load('easy_test_attention_mask.npy')
easy_test_token_type_ids = np.load('easy_test_token_type_ids.npy')

In [ ]:
easy_train_input_ids = np.load('easy_train_input_ids.npy')
easy_train_attention_mask = np.load('easy_train_attention_mask.npy')
easy_train_token_type_ids = np.load('easy_train_token_type_ids.npy')

In [ ]:
def calculate_scores(qa_predictions: str) -> None:
    """
    Uses the scores per answer choice to compute the QA score
    :param qa_predictions: QA predictions with scores per choice
    """
    with open(qa_predictions, 'r') as qa_handle:
        total_score = 0
        num_questions = 0
        partially_correct = 0
        correct = 0
        incorrect = 0
        for line in qa_handle:
            json_line = json.loads(line)
            answer_choices = json_line["question"]["choices"]
            max_choice_score = max(answer_choices, key=itemgetter("score"))["score"]
            # Collect all answer choices with the same score
            selected_answers = [choice["label"] for choice in answer_choices
                                if choice["score"] == max_choice_score]
            answer_key = json_line["answerKey"]

            if answer_key in selected_answers:
                question_score = 1 / len(selected_answers)
                if question_score < 1:
                    partially_correct += 1
                else:
                    correct += 1
            else:
                question_score = 0
                incorrect += 1
            total_score += question_score
            num_questions += 1

        print("""Metrics:
       Total Points={:.2f}
       Questions:{}
       Exam Score:{:.2f}
          Correct:      {}
          Incorrect:    {}
          Partial:      {}
                """.format(total_score, num_questions, (total_score / num_questions)*100,
                           correct, incorrect, partially_correct))


In [ ]:
tf.keras.backend.clear_session()
pre_trained_model = TFBertForMultipleChoice.from_pretrained('bert-base-uncased')

model_input_ids = Input(shape=(5,512,), name='input_tokens', dtype='int32')
masks_input = Input(shape=(5,512,), name='attention_mask', dtype='int32')
model_token_type_ids = Input(shape=(5,512,), name='token_type_ids', dtype='int32')

x = {'input_ids':model_input_ids,
        'attention_mask':masks_input,
        'token_type_ids':model_token_type_ids}

x = pre_trained_model(x)['logits']
outputs = Dense(5, activation='softmax')(x)

model = Model(inputs=[model_input_ids, masks_input,model_token_type_ids], outputs=outputs)

optimizer = tf.keras.optimizers.Adam(learning_rate=1e-5)
loss = tf.keras.losses.CategoricalCrossentropy()
model.compile(optimizer=optimizer, 
                loss=loss, metrics=['accuracy'])

All model checkpoint layers were used when initializing TFBertForMultipleChoice.

Some layers of TFBertForMultipleChoice were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [4]:
easy_train_labels = np.load('easy_train_labels.npy')

In [5]:
y=tf.keras.utils.to_categorical(easy_train_labels.ravel())

In [7]:
tf.config.run_functions_eagerly(True)

In [ ]:
early_stop = EarlyStopping(patience=2, monitor='val_accuracy')

model.fit(x=[easy_train_input_ids, easy_train_attention_mask, easy_train_token_type_ids], y=y,
          epochs=3,batch_size=2)

/usr/local/lib/python3.7/dist-packages/tensorflow/python/data/ops/structured_function.py:265: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  "Even though the `tf.config.experimental_run_functions_eagerly` "


Epoch 1/3
1126/1126 [==============================] - 14754s 13s/step - loss: 1.5006 - accuracy: 0.2386
Epoch 2/3
1126/1126 [==============================] - 14955s 13s/step - loss: 1.4149 - accuracy: 0.2612
Epoch 3/3
 987/1126 [=========================>....] - ETA: 30:59 - loss: 1.3503 - accuracy: 0.3404

In [ ]:
model.save('bert_model')

In [ ]:
model.save_weights('bert_weights')

In [ ]:
model.load_weights('bert_weights')

In [ ]:
easy_dev_labels = np.load('easy_dev_labels.npy')
easy_test_labels = np.load('easy_test_labels.npy')

In [ ]:
dev_preds = model.predict([easy_dev_input_ids,easy_dev_attention_mask,easy_dev_token_type_ids])
dev_preds_max = tf.argmax(dev_preds, axis=1)

/usr/local/lib/python3.7/dist-packages/tensorflow/python/data/ops/structured_function.py:265: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  "Even though the `tf.config.experimental_run_functions_eagerly` "


In [ ]:
print(f'Accuracy score on easy dev set is {accuracy_score(easy_dev_labels,dev_preds_max)}.')

Accuracy score on easy dev set is 0.2771929824561403.


In [ ]:
test_preds = model.predict([easy_test_input_ids,easy_test_attention_mask,easy_test_token_type_ids])
test_preds_max = tf.argmax(test_preds, axis=1)

/usr/local/lib/python3.7/dist-packages/tensorflow/python/data/ops/structured_function.py:265: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  "Even though the `tf.config.experimental_run_functions_eagerly` "


In [ ]:
print(f'Accuracy score on easy test set is {accuracy_score(easy_test_labels,test_preds_max)}.')

Accuracy score on easy test set is 0.25084175084175087.


## RoBERTa Model.


In [ ]:
from transformers import RobertaTokenizer, TFRobertaForMultipleChoice

### Preparing data according to RoBERTa.

In [ ]:
tokenizer = RobertaTokenizer.from_pretrained('roberta-base', do_lower_case=True)

Downloading:   0%|          | 0.00/878k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/446k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/481 [00:00<?, ?B/s]

In [ ]:
MAX_LEN=128

In [ ]:
def arc_preprocessor(dataset, tokenizer):
    '''
    This function will convert a given article, question, choices in a format:

    <s> article </s> </s> question </s> </s> choices[0] </s>
    <s> article </s> </s> question </s> </s> choices[1] </s>
    <s> article </s> </s> question </s> </s> choices[2] </s>
    <s> article </s> </s> question </s> </s> choices[3] </s>

    After converting in this format the data will be tokenized using a given tokenizer.
    This function will return 4 arrays namely, input_ids, attention_mask, token_type_ids and labels.

    individual input_ids, token_type_ids, attention_mask shape will be as: [num_choices, max_seq_length]
    '''
    global MAX_LEN
    all_input_ids = []
    all_attention_mask = []
    all_token_type_ids = []

    for i in range(len(dataset)):
        
        context = ' '.join(dataset['context'].iloc[i].split()[:400]) #Limiting the maximum length of context to 400 words.
        question = dataset['only_question'].iloc[i]
        options = dataset['options_list'].iloc[i]
        choice_features = []

        for j in range(len(options)):

            option = options[j]
            input_string = '<s>' + ' ' + context + ' ' + '</s>' + ' ' + '</s>' + ' ' + question + ' ' + '</s>' + ' ' + '</s>' + ' ' + option + ' ' + '</s>'
            input_string = re.sub(r'\s+', ' ', input_string)

            input_ids = tokenizer(input_string,
                               max_length=MAX_LEN,
                               add_special_tokens=False, truncation='only_first')['input_ids']
            
            attention_mask = [1] * len(input_ids)

            padding_id = tokenizer.pad_token_id
            padding_length = MAX_LEN - len(input_ids)

            input_ids = input_ids + [padding_id]*padding_length
            attention_mask = attention_mask + [0]*padding_length

            assert len(input_ids) == MAX_LEN
            assert len(attention_mask) == MAX_LEN

            choice_features.append({'input_ids':input_ids,
                                    'attention_mask':attention_mask})

        all_input_ids.append(np.asarray([cf['input_ids'] for cf in choice_features], dtype='int32'))
        all_attention_mask.append(np.asarray([cf['attention_mask'] for cf in choice_features], dtype='int32'))

    return all_input_ids, all_attention_mask

In [ ]:
easy_train_input_ids, easy_train_attention_mask = arc_preprocessor(df_easy_train, tokenizer)
easy_dev_input_ids, easy_dev_attention_mask = arc_preprocessor(df_easy_dev, tokenizer)
easy_test_input_ids, easy_test_attention_mask = arc_preprocessor(df_easy_test, tokenizer)

In [ ]:
easy_train_input_ids = np.asarray(easy_train_input_ids, dtype='int32')
easy_train_attention_mask = np.asarray(easy_train_attention_mask, dtype='int32')

In [ ]:
easy_dev_input_ids = np.asarray(easy_dev_input_ids, dtype='int32')
easy_dev_attention_mask = np.asarray(easy_dev_attention_mask, dtype='int32')

In [ ]:
easy_test_input_ids = np.asarray(easy_test_input_ids, dtype='int32')
easy_test_attention_mask = np.asarray(easy_test_attention_mask, dtype='int32')

In [ ]:
np.save('easy_train_input_ids.npy', easy_train_input_ids)
np.save('easy_train_attention_mask.npy', easy_train_attention_mask)

In [ ]:
np.save('easy_dev_input_ids.npy', easy_dev_input_ids)
np.save('easy_dev_attention_mask.npy', easy_dev_attention_mask)

In [ ]:
np.save('easy_test_input_ids.npy', easy_test_input_ids)
np.save('easy_test_attention_mask.npy', easy_test_attention_mask)

## Training RoBERTa.

In [ ]:
easy_train_input_ids = np.load('/content/drive/MyDrive/ARC/RoBERTa_2 files/easy_train_input_ids.npy')
easy_train_attention_mask = np.load('/content/drive/MyDrive/ARC/RoBERTa_2 files/easy_train_attention_mask.npy')

In [ ]:
easy_dev_input_ids = np.load('/content/drive/MyDrive/ARC/RoBERTa_2 files/easy_dev_input_ids.npy')
easy_dev_attention_mask = np.load('/content/drive/MyDrive/ARC/RoBERTa_2 files/easy_dev_attention_mask.npy')

In [ ]:
easy_test_input_ids = np.load('/content/drive/MyDrive/ARC/RoBERTa_2 files/easy_test_input_ids.npy')
easy_test_attention_mask = np.load('/content/drive/MyDrive/ARC/RoBERTa_2 files/easy_test_attention_mask.npy')

In [ ]:
strategy = tf.distribute.TPUStrategy(resolver)

INFO:tensorflow:Found TPU system:


INFO:tensorflow:Found TPU system:


INFO:tensorflow:*** Num TPU Cores: 8


INFO:tensorflow:*** Num TPU Cores: 8


INFO:tensorflow:*** Num TPU Workers: 1


...

INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:worker/replica:0/task:0/device:TPU:7, TPU, 0, 0)


INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:worker/replica:0/task:0/device:TPU_SYSTEM:0, TPU_SYSTEM, 0, 0)


INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:worker/replica:0/task:0/device:TPU_SYSTEM:0, TPU_SYSTEM, 0, 0)


INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:worker/replica:0/task:0/device:XLA_CPU:0, XLA_CPU, 0, 0)


INFO:tensorflow:*** Available Device: _DeviceAttributes(/job:worker/replica:0/task:0/device:XLA_CPU:0, XLA_CPU, 0, 0)


In [ ]:
#with strategy.scope():
pre_trained_model = TFRobertaForMultipleChoice.from_pretrained('roberta-base')

model_input_ids = Input(shape=(5,128,), name='input_tokens', dtype='int32')
masks_input = Input(shape=(5,128,), name='attention_mask', dtype='int32')

x =  {'input_ids':model_input_ids,
            'attention_mask':masks_input}

x = pre_trained_model(x)['logits']
outputs = Dense(5, activation='softmax')(x)

model = Model(inputs=[model_input_ids, masks_input], outputs=outputs)

model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate=1e-5),
              loss=tf.keras.losses.CategoricalCrossentropy(),
              metrics=['accuracy'])

All model checkpoint layers were used when initializing TFRobertaForMultipleChoice.

Some layers of TFRobertaForMultipleChoice were not initialized from the model checkpoint at roberta-base and are newly initialized: ['classifier']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
valid_y = tf.keras.utils.to_categorical(easy_dev_labels, num_classes=5)

In [ ]:
model.fit(x=[easy_train_input_ids, easy_train_attention_mask], y=tf.keras.utils.to_categorical(easy_train_labels),
          batch_size=8, epochs=5,
          validation_data=([easy_dev_input_ids, easy_dev_attention_mask], valid_y),
          validation_batch_size=8)

Epoch 1/5


/usr/local/lib/python3.7/dist-packages/tensorflow/python/data/ops/structured_function.py:265: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  "Even though the `tf.config.experimental_run_functions_eagerly` "


282/282 [==============================] - 2837s 10s/step - loss: 1.5670 - accuracy: 0.2355 - val_loss: 1.5737 - val_accuracy: 0.2070
Epoch 2/5
282/282 [==============================] - 2838s 10s/step - loss: 1.5595 - accuracy: 0.2377 - val_loss: 1.5731 - val_accuracy: 0.2070
Epoch 3/5
282/282 [==============================] - 2841s 10s/step - loss: 1.5570 - accuracy: 0.2377 - val_loss: 1.5700 - val_accuracy: 0.2070
Epoch 4/5
282/282 [==============================] - 2848s 10s/step - loss: 1.5568 - accuracy: 0.2377 - val_loss: 1.5689 - val_accuracy: 0.2070
Epoch 5/5
282/282 [==============================] - 2857s 10s/step - loss: 1.5545 - accuracy: 0.2377 - val_loss: 1.5675 - val_accuracy: 0.2070


In [ ]:
model.save('roberta_model')

In [ ]:
model.save_weights('roberta_weights')

In [ ]:
test_preds = model.predict([easy_test_input_ids,easy_test_attention_mask])
test_preds_max = tf.argmax(test_preds, axis=1)

/usr/local/lib/python3.7/dist-packages/tensorflow/python/data/ops/structured_function.py:265: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  "Even though the `tf.config.experimental_run_functions_eagerly` "


In [ ]:
print(f'Accuracy score on easy test set is {accuracy_score(easy_test_labels,test_preds_max)}.')

Accuracy score on easy test set is 0.2361111111111111.


## XLNET Model.

### Preparing data according to XLNET.

In [ ]:
from transformers import AutoTokenizer

In [ ]:
tokenizer = AutoTokenizer.from_pretrained('xlnet-base-cased', do_lower_case=True)

Downloading:   0%|          | 0.00/760 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/779k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.32M [00:00<?, ?B/s]

In [ ]:
MAX_LEN=128

In [ ]:
def arc_preprocessor(dataset, tokenizer):
    '''
    This function will convert a given article, question, choices in a format:

    article <sep> question choices[0] <sep> <cls>
    article <sep> question choices[1] <sep> <cls>
    article <sep> question choices[2] <sep> <cls>
    article <sep> question choices[3] <sep> <cls>

    After converting in this format the data will be tokenized using a given tokenizer.
    This function will return 4 arrays namely, input_ids, attention_mask, token_type_ids and labels.

    individual input_ids, token_type_ids, attention_mask shape will be as: [num_choices, max_seq_length]
    '''
    global MAX_LEN
    all_input_ids = []
    all_attention_mask = []
    all_token_type_ids = []

    for i in range(len(dataset)):
        
        context = ' '.join(dataset['context'].iloc[i].split()[:400]) #Limiting the maximum length of context to 400 words.
        question = dataset['only_question'].iloc[i]
        options = dataset['options_list'].iloc[i]
        choice_features = []

        for j in range(len(options)):

            option = options[j]
            input_string = '<s>' + ' ' + context + ' ' + '</s>' + ' ' + question + ' ' + '</s>' + ' ' + option + ' ' + '</s>'
            input_string = re.sub(r'\s+', ' ', input_string)

            input_ids = tokenizer(input_string,
                               max_length=MAX_LEN,
                               add_special_tokens=False)['input_ids']
            
            attention_mask = [1] * len(input_ids)

            padding_id = tokenizer.pad_token_id
            padding_length = MAX_LEN - len(input_ids)

            input_ids = input_ids + [padding_id]*padding_length
            attention_mask = attention_mask + [0]*padding_length

            assert len(input_ids) == MAX_LEN
            assert len(attention_mask) == MAX_LEN

            choice_features.append({'input_ids':input_ids,
                                    'attention_mask':attention_mask})

        all_input_ids.append(np.asarray([cf['input_ids'] for cf in choice_features], dtype='int32'))
        all_attention_mask.append(np.asarray([cf['attention_mask'] for cf in choice_features], dtype='int32'))

    return all_input_ids, all_attention_mask

In [ ]:
easy_train_input_ids, easy_train_attention_mask = arc_preprocessor(df_easy_train, tokenizer)
easy_dev_input_ids, easy_dev_attention_mask = arc_preprocessor(df_easy_dev, tokenizer)
easy_test_input_ids, easy_test_attention_mask = arc_preprocessor(df_easy_test, tokenizer)

Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.


In [ ]:
easy_train_input_ids = np.asarray(easy_train_input_ids, dtype='int32')
easy_train_attention_mask = np.asarray(easy_train_attention_mask, dtype='int32')

In [ ]:
easy_dev_input_ids = np.asarray(easy_dev_input_ids, dtype='int32')
easy_dev_attention_mask = np.asarray(easy_dev_attention_mask, dtype='int32')

In [ ]:
easy_test_input_ids = np.asarray(easy_test_input_ids, dtype='int32')
easy_test_attention_mask = np.asarray(easy_test_attention_mask, dtype='int32')

In [ ]:
np.save('easy_train_input_ids.npy', easy_train_input_ids)
np.save('easy_train_attention_mask.np', easy_train_attention_mask)

In [ ]:
np.save('easy_dev_input_ids.npy', easy_dev_input_ids)
np.save('easy_dev_attention_mask.npy', easy_dev_attention_mask)

In [ ]:
np.save('easy_test_input_ids.npy', easy_test_input_ids)
np.save('easy_test_attention_mask.npy', easy_test_attention_mask)

### Training XLNet.

In [ ]:
easy_train_input_ids = np.load('/content/drive/MyDrive/ARC/XLNet files/easy_train_input_ids.npy')
easy_train_attention_mask = np.load('/content/drive/MyDrive/ARC/XLNet files/easy_train_attention_mask.npy')

In [ ]:
easy_dev_input_ids = np.load('/content/drive/MyDrive/ARC/XLNet files/easy_dev_input_ids.npy')
easy_dev_attention_mask = np.load('/content/drive/MyDrive/ARC/XLNet files/easy_dev_attention_mask.npy')

In [ ]:
easy_test_input_ids = np.load('/content/drive/MyDrive/ARC/XLNet files/easy_test_input_ids.npy')
easy_test_attention_mask = np.load('/content/drive/MyDrive/ARC/XLNet files/easy_test_attention_mask.npy')

In [ ]:
from transformers import TFXLNetForMultipleChoice

In [ ]:
strategy = tf.distribute.experimental.TPUStrategy(resolver)

In [ ]:
easy_train_dict = {'input_tokens':easy_train_input_ids,
                   'attention_mask':easy_train_attention_mask}

viola = tf.data.Dataset.from_tensor_slices((easy_train_dict,tf.keras.utils.to_categorical(easy_train_labels.values)))

In [ ]:
viola = viola.shuffle(32).batch(8).cache().prefetch(tf.data.experimental.AUTOTUNE)

In [ ]:
easy_dev_dict = {'input_tokens':easy_dev_input_ids,
                   'attention_mask':easy_dev_attention_mask}

viola_dev = tf.data.Dataset.from_tensor_slices((easy_dev_dict,tf.keras.utils.to_categorical(easy_dev_labels.values, num_classes=5)))

In [ ]:
viola_dev = viola_dev.shuffle(32).batch(8).cache().prefetch(tf.data.experimental.AUTOTUNE)

In [ ]:

pre_trained_model = TFXLNetForMultipleChoice.from_pretrained('xlnet-base-cased')

model_input_ids = Input(shape=(5,128,), name='input_tokens', dtype='int32')
masks_input = Input(shape=(5,128,), name='attention_mask', dtype='int32')

x =  {'input_ids':model_input_ids,
            'attention_mask':masks_input}

x = pre_trained_model(x)['logits']
    # x = Dense(64, activation='relu', kernel_initializer='he_normal')(x)
    # x = Dropout(0.2)(x)
outputs = Dense(5, activation='softmax')(x)

model = Model(inputs=[model_input_ids, masks_input], outputs=outputs)

model.compile(optimizer=tf.keras.optimizers.Adam(learning_rate=5e-6),
                loss=tf.keras.losses.CategoricalCrossentropy(),
                metrics=['accuracy'])

Some layers from the model checkpoint at xlnet-base-cased were not used when initializing TFXLNetForMultipleChoice: ['lm_loss']
- This IS expected if you are initializing TFXLNetForMultipleChoice from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFXLNetForMultipleChoice from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some layers of TFXLNetForMultipleChoice were not initialized from the model checkpoint at xlnet-base-cased and are newly initialized: ['sequence_summary', 'logits_proj']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
model.fit(viola, epochs=4)

Epoch 1/4


  1/282 [..............................] - ETA: 1:01:51 - loss: 1.7145 - accuracy: 0.0000e+00WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_for_multiple_choice_1/transformer/mask_emb:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choic

  2/282 [..............................] - ETA: 59:03 - loss: 1.7174 - accuracy: 0.0000e+00  WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_for_multiple_choice_1/transformer/mask_emb:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choic

  3/282 [..............................] - ETA: 59:14 - loss: 1.7117 - accuracy: 0.0833    WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_for_multiple_choice_1/transformer/mask_emb:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_

  4/282 [..............................] - ETA: 59:09 - loss: 1.6918 - accuracy: 0.1250WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_for_multiple_choice_1/transformer/mask_emb:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/tr

...

278/282 [============================>.] - ETA: 51s - loss: 1.4998 - accuracy: 0.3134 WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_for_multiple_choice_1/transformer/mask_emb:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/tra

279/282 [============================>.] - ETA: 38s - loss: 1.5001 - accuracy: 0.3132WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_for_multiple_choice_1/transformer/mask_emb:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/tran

280/282 [============================>.] - ETA: 25s - loss: 1.4992 - accuracy: 0.3143WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_for_multiple_choice_1/transformer/mask_emb:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/tran

281/282 [============================>.] - ETA: 12s - loss: 1.4993 - accuracy: 0.3136WARNING:tensorflow:Gradients do not exist for variables ['tfxl_net_for_multiple_choice_1/transformer/mask_emb:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._0/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._1/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._2/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._3/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/r_s_bias:0', 'tfxl_net_for_multiple_choice_1/transformer/layer_._4/rel_attn/seg_embed:0', 'tfxl_net_for_multiple_choice_1/tran

282/282 [==============================] - 3621s 13s/step - loss: 1.4994 - accuracy: 0.3132


In [ ]:
model.save('xlnet_model')

In [ ]:
model.save_weights('xlnet_weights')

In [ ]:
dev_preds = model.predict([easy_dev_input_ids,easy_dev_attention_mask])
dev_preds_max = tf.argmax(dev_preds, axis=1)

/usr/local/lib/python3.7/dist-packages/tensorflow/python/data/ops/structured_function.py:265: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  "Even though the `tf.config.experimental_run_functions_eagerly` "


In [ ]:
print(f'Accuracy score on easy dev set is {accuracy_score(easy_dev_labels,dev_preds_max)}.')

Accuracy score on easy dev set is 0.2719298245614035.


In [ ]:
test_preds = model.predict([easy_test_input_ids,easy_test_attention_mask])
test_preds_max = tf.argmax(test_preds, axis=1)

/usr/local/lib/python3.7/dist-packages/tensorflow/python/data/ops/structured_function.py:265: UserWarning: Even though the `tf.config.experimental_run_functions_eagerly` option is set, this option does not apply to tf.data functions. To force eager execution of tf.data functions, please use `tf.data.experimental.enable_debug_mode()`.
  "Even though the `tf.config.experimental_run_functions_eagerly` "


In [ ]:
print(f'Accuracy score on easy test set is {accuracy_score(easy_test_labels,test_preds_max)}.')

Accuracy score on easy test set is 0.265993265993266.


## Fine tuning Unified QA on ARC

In [70]:
from transformers import AutoTokenizer, T5ForConditionalGeneration

tokenizer = AutoTokenizer.from_pretrained('t5-small')

/usr/local/lib/python3.7/dist-packages/transformers/models/t5/tokenization_t5_fast.py:166: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-small automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  FutureWarning,


In [71]:
MAX_LEN = 128
decoder_max_len = 30

In [72]:
def arc_preprocessor(dataset, tokenizer):
    '''
    This function will convert a given context, question, choices in a format:

    input: question \n options \n context </s>
    target: label </s>

    After converting in this format the data will be tokenized using a given tokenizer.
    This function will return 4 arrays namely, input_ids, attention_mask, token_type_ids and labels.
    '''
    global MAX_LEN
    all_input_ids = []
    all_attention_mask = []
    all_decoder_input_ids = []
    all_labels = []

    for i in range(len(dataset)):
        
        context = ' '.join(dataset['context'].iloc[i].split()[:350]) #Limiting the maximum length of context to 350 words.
        question = dataset['only_question'].iloc[i]
        options = dataset['only_answers'].iloc[i]
        target = dataset['Answer'].iloc[i]
        choice_features = []

        input_string = question + ' ' + '\\n' + ' ' + options + ' ' + '</s>'
        decoder_input = tokenizer.pad_token + ' ' + target
        target = target + ' ' + '</s>'

        input_ids = tokenizer.encode(input_string, truncation=True, max_length=MAX_LEN)
        decoder_input_ids = tokenizer.encode(decoder_input, max_length=decoder_max_len, truncation=True) #Max length of a answer is 23
        labels = tokenizer.encode(target, max_length=decoder_max_len, truncation=True)

        attention_mask = [1] * len(input_ids)

        padding_id = tokenizer.pad_token_id
        padding_length = MAX_LEN - len(input_ids)

        input_ids = input_ids + [padding_id]*padding_length
        attention_mask = attention_mask + [0]*padding_length

        deocder_padding_length = decoder_max_len - len(decoder_input_ids)

        decoder_input_ids = decoder_input_ids + [padding_id]*deocder_padding_length
        labels = labels + [padding_id]*deocder_padding_length

        assert len(input_ids) == MAX_LEN
        assert len(attention_mask) == MAX_LEN

        all_input_ids.append(np.asarray(input_ids, dtype='int32'))
        all_attention_mask.append(np.asarray(attention_mask, dtype='int32'))
        all_decoder_input_ids.append(np.asarray(decoder_input_ids, dtype='int32'))
        all_labels.append(np.asarray(labels, dtype='int32'))

    return all_input_ids, all_attention_mask, all_decoder_input_ids, all_labels

In [ ]:
easy_train_input_ids, easy_train_attention_mask, easy_train_decoder_input_ids, easy_train_labels = arc_preprocessor(df_easy_train, tokenizer)

In [ ]:
easy_dev_input_ids, easy_dev_attention_mask, easy_dev_decoder_input_ids, easy_dev_labels = arc_preprocessor(df_easy_dev, tokenizer)

In [ ]:
easy_test_input_ids, easy_test_attention_mask, _, easy_test_labels = arc_preprocessor(df_easy_test, tokenizer)

challenge

In [73]:
challenge_train_input_ids, challenge_train_attention_mask, challenge_train_decoder_input_ids, challenge_train_labels = arc_preprocessor(df_challenge_train, tokenizer)

In [74]:
challenge_dev_input_ids, challenge_dev_attention_mask, challenge_dev_decoder_input_ids, challenge_dev_labels = arc_preprocessor(df_challenge_dev, tokenizer)

In [75]:
challenge_test_input_ids, challenge_test_attention_mask, _,challenge_test_labels = arc_preprocessor(df_challenge_test, tokenizer)

In [ ]:
easy_train_input_ids = np.asarray(easy_train_input_ids, dtype='int32')
easy_train_attention_mask = np.asarray(easy_train_attention_mask, dtype='int32')
easy_train_decoder_input_ids = np.asarray(easy_train_decoder_input_ids, dtype='int32')
easy_train_labels = np.asarray(easy_train_labels, dtype='int32')

In [ ]:
easy_dev_input_ids = np.asarray(easy_dev_input_ids, dtype='int32')
easy_dev_attention_mask = np.asarray(easy_dev_attention_mask, dtype='int32')
easy_dev_decoder_input_ids = np.asarray(easy_dev_decoder_input_ids, dtype='int32')
easy_dev_labels = np.asarray(easy_dev_labels, dtype='int32')

In [ ]:
easy_test_input_ids = np.asarray(easy_test_input_ids, dtype='int32')
easy_test_attention_mask = np.asarray(easy_test_attention_mask, dtype='int32')
easy_test_labels = np.asarray(easy_test_labels, dtype='int32')

challenge

In [76]:
challenge_train_input_ids = np.asarray(challenge_train_input_ids, dtype='int32')
challenge_train_attention_mask = np.asarray(challenge_train_attention_mask, dtype='int32')
challenge_train_decoder_input_ids = np.asarray(challenge_train_decoder_input_ids, dtype='int32')
challenge_train_labels = np.asarray(challenge_train_labels, dtype='int32')

In [77]:
challenge_dev_input_ids = np.asarray(challenge_dev_input_ids, dtype='int32')
challenge_dev_attention_mask = np.asarray(challenge_dev_attention_mask, dtype='int32')
challenge_dev_decoder_input_ids = np.asarray(challenge_dev_decoder_input_ids, dtype='int32')
challenge_dev_labels = np.asarray(challenge_dev_labels, dtype='int32')

In [78]:
challenge_test_input_ids = np.asarray(challenge_test_input_ids, dtype='int32')
challenge_test_attention_mask = np.asarray(challenge_test_attention_mask, dtype='int32')
challenge_test_labels = np.asarray(challenge_test_labels, dtype='int32')

In [ ]:
np.save('easy_train_input_ids.npy', easy_train_input_ids)
np.save('easy_train_attention_mask.npy', easy_train_attention_mask)
np.save('easy_train_decoder_input_ids.npy', easy_train_decoder_input_ids)
np.save('easy_train_labels.npy', easy_train_labels)

In [ ]:
np.save('easy_dev_input_ids.npy', easy_dev_input_ids)
np.save('easy_dev_attention_mask.npy', easy_dev_attention_mask)
np.save('easy_dev_decoder_input_ids.npy', easy_dev_decoder_input_ids)
np.save('easy_dev_labels.npy', easy_dev_labels)

In [ ]:
np.save('easy_test_input_ids.npy', easy_test_input_ids)
np.save('easy_test_attention_mask.npy', easy_test_attention_mask)
np.save('easy_test_labels.npy', easy_test_labels)

challenge

In [79]:
np.save('challenge_train_input_ids.npy', challenge_train_input_ids)
np.save('challenge_train_attention_mask.npy', challenge_train_attention_mask)
np.save('challenge_train_decoder_input_ids.npy', challenge_train_decoder_input_ids)
np.save('challenge_train_labels.npy', challenge_train_labels)

In [80]:
np.save('challenge_dev_input_ids.npy', challenge_dev_input_ids)
np.save('challenge_dev_attention_mask.npy', challenge_dev_attention_mask)
np.save('challenge_dev_decoder_input_ids.npy', challenge_dev_decoder_input_ids)
np.save('challenge_dev_labels.npy', challenge_dev_labels)

In [81]:
np.save('challenge_test_input_ids.npy', challenge_test_input_ids)
np.save('challeng_test_attention_mask.npy', challenge_test_attention_mask)
np.save('challeng_test_labels.npy',challenge_test_labels)

### T5 Training.

In [3]:
easy_train_input_ids = np.load('easy_train_input_ids.npy')
easy_train_attention_mask = np.load('easy_train_attention_mask.npy')
easy_train_decoder_input_ids = np.load('easy_train_decoder_input_ids.npy')
easy_train_labels = np.load('easy_train_labels.npy')

In [4]:
easy_dev_input_ids = np.load('easy_dev_input_ids.npy')
easy_dev_attention_mask = np.load('easy_dev_attention_mask.npy')
easy_dev_decoder_input_ids = np.load('easy_dev_decoder_input_ids.npy')
easy_dev_labels = np.load('easy_dev_labels.npy')

In [5]:
easy_test_input_ids = np.load('easy_test_input_ids.npy')
easy_test_attention_mask = np.load('easy_test_attention_mask.npy')
easy_test_labels = np.load('easy_test_labels.npy')

challenge

In [82]:
challenge_train_input_ids = np.load('challenge_train_input_ids.npy')
challenge_train_attention_mask = np.load('challenge_train_attention_mask.npy')
challenge_train_decoder_input_ids = np.load('challenge_train_decoder_input_ids.npy')
challenge_train_labels = np.load('challenge_train_labels.npy')

In [83]:
challenge_dev_input_ids = np.load('challenge_dev_input_ids.npy')
challenge_dev_attention_mask = np.load('challenge_dev_attention_mask.npy')
challenge_dev_decoder_input_ids = np.load('challenge_dev_decoder_input_ids.npy')
challenge_dev_labels = np.load('challenge_dev_labels.npy')

In [86]:
challenge_test_input_ids = np.load('challenge_test_input_ids.npy')
challenge_test_attention_mask = np.load('challeng_test_attention_mask.npy')
challenge_test_labels = np.load('challeng_test_labels.npy')

In [6]:
import torch
from torch.utils.data import Dataset, DataLoader

In [7]:
class arc_dataset(Dataset):

    def __init__(self, input_ids, attention_mask, decoder_input_ids, labels):
        self.input_ids = input_ids
        self.attention_mask = attention_mask
        self.decoder_input_ids = decoder_input_ids
        self.labels = labels
    
    def __len__(self):
        return len(self.input_ids)
    
    def __getitem__(self, idx):
        if torch.is_tensor(idx):
            idx = idx.tolist()
        
        sample = {'input_ids': self.input_ids[idx],
                  'attention_mask': self.attention_mask[idx],
                  'decoder_input_ids':self.decoder_input_ids[idx],
                  'labels':self.labels[idx]}
        
        return sample

In [8]:
train_dataset = arc_dataset(easy_train_input_ids, easy_train_attention_mask, easy_train_decoder_input_ids, easy_train_labels)

In [9]:
dev_dataset = arc_dataset(easy_dev_input_ids, easy_dev_attention_mask, easy_dev_decoder_input_ids, easy_dev_labels)

In [10]:
train_dataloader = DataLoader(train_dataset, batch_size=4, shuffle=True, num_workers=4)
dev_dataloader = DataLoader(dev_dataset, batch_size=4, shuffle=True, num_workers=4)

In [11]:
from transformers import T5ForConditionalGeneration, AdamW

In [12]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model = T5ForConditionalGeneration.from_pretrained("allenai/unifiedqa-t5-base")

model.cuda()

Downloading:   0%|          | 0.00/1.21k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/850M [00:00<?, ?B/s]

T5ForConditionalGeneration(
  (shared): Embedding(32128, 768)
  (encoder): T5Stack(
    (embed_tokens): Embedding(32128, 768)
    (block): ModuleList(
      (0): T5Block(
        (layer): ModuleList(
          (0): T5LayerSelfAttention(
            (SelfAttention): T5Attention(
              (q): Linear(in_features=768, out_features=768, bias=False)
              (k): Linear(in_features=768, out_features=768, bias=False)
              (v): Linear(in_features=768, out_features=768, bias=False)
              (o): Linear(in_features=768, out_features=768, bias=False)
              (relative_attention_bias): Embedding(32, 12)
            )
            (layer_norm): T5LayerNorm()
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (1): T5LayerFF(
            (DenseReluDense): T5DenseActDense(
              (wi): Linear(in_features=768, out_features=3072, bias=False)
              (wo): Linear(in_features=3072, out_features=768, bias=False)
              (dropout): Dro

In [13]:
from transformers import get_linear_schedule_with_warmup

In [14]:
# This variable contains all of the hyperparemeter information our training loop needs
# Parameters:
lr = 1e-4
max_grad_norm = 1.0
num_training_steps = 1000
num_warmup_steps = 100
warmup_proportion = float(num_warmup_steps) / float(num_training_steps)  # 0.1

### In Transformers, optimizer and schedules are splitted and instantiated like this:
optimizer = AdamW(model.parameters(), lr=lr)  # To reproduce BertAdam specific behavior set correct_bias=False
scheduler = get_linear_schedule_with_warmup(optimizer, num_warmup_steps=num_warmup_steps, num_training_steps=num_training_steps)  # PyTorch scheduler

# Store our loss and accuracy for plotting
train_loss_set = []

/usr/local/lib/python3.7/dist-packages/transformers/optimization.py:310: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  FutureWarning,


In [15]:
# Number of training epochs (authors recommend between 2 and 4)
epochs = 4

In [16]:
for epoch in range(epochs):
    # Training
    # Set our model to training mode (as opposed to evaluation mode)
    model.train()
    # Tracking variables
    tr_loss = 0
    nb_tr_examples, nb_tr_steps = 0, 0

    running_loss = 0

    # Train the data for one epoch
    for step, batch in enumerate(train_dataloader):
        # Add batch to GPU
        # batch = tuple(t.to(device) for t in batch)

        # Unpack the inputs from our dataloader
        b_input_ids, b_input_mask, b_decoder_ids, b_labels = batch['input_ids'], batch['attention_mask'], batch['decoder_input_ids'], batch['labels']

        ###############Bug fix code####################
        b_input_ids = b_input_ids.type(torch.LongTensor)
        b_input_mask = b_input_mask.type(torch.LongTensor)
        b_decoder_ids = b_decoder_ids.type(torch.LongTensor)
        b_labels = b_labels.type(torch.LongTensor)

        b_input_ids = b_input_ids.to(device)
        b_input_mask = b_input_mask.to(device)
        b_decoder_ids = b_decoder_ids.to(device)
        b_labels = b_labels.to(device)
         ############################################
        # Clear out the gradients (by default they accumulate)
        optimizer.zero_grad()
        
        # Forward pass
        outputs = model(input_ids = b_input_ids, attention_mask=b_input_mask, decoder_input_ids=b_decoder_ids, labels=b_labels)
        loss, logits = outputs[:2]

        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_grad_norm)  # Gradient clipping is not in AdamW anymore (so you can use amp without issue)
        optimizer.step()
        scheduler.step()

        running_loss = loss.item()

        if step%100 == 99:
            print(f'Epoch:{epoch} Batch:{step} Loss:{running_loss}')
            running_loss = 0

print('Training finished.')

Epoch:0 Batch:99 Loss:0.2904745638370514
Epoch:0 Batch:199 Loss:0.05165645107626915
Epoch:0 Batch:299 Loss:0.055354420095682144
Epoch:0 Batch:399 Loss:0.08666642010211945
Epoch:0 Batch:499 Loss:0.018585985526442528
Epoch:1 Batch:99 Loss:0.06960447132587433
Epoch:1 Batch:199 Loss:0.012116119265556335
Epoch:1 Batch:299 Loss:0.00016586111451033503
Epoch:1 Batch:399 Loss:0.0026934188790619373
Epoch:1 Batch:499 Loss:0.09360504895448685
Epoch:2 Batch:99 Loss:0.004919534549117088
Epoch:2 Batch:199 Loss:0.041171468794345856
Epoch:2 Batch:299 Loss:0.02119266986846924
Epoch:2 Batch:399 Loss:0.0021474554669111967
Epoch:2 Batch:499 Loss:0.01954750530421734
Epoch:3 Batch:99 Loss:0.04077821224927902
Epoch:3 Batch:199 Loss:0.009727207012474537
Epoch:3 Batch:299 Loss:0.013246147893369198
Epoch:3 Batch:399 Loss:0.01819094642996788
Epoch:3 Batch:499 Loss:0.0009731421596370637
Training finished.


In [17]:
loss

tensor(2.7098e-05, device='cuda:0', grad_fn=<NllLossBackward0>)

In [18]:
model.save_pretrained('Unified_QA_2')

In [110]:
model.save_pretrained('drive/MyDrive/ARC/Unified_QA/')

### Inference.

In [19]:
from transformers import T5ForConditionalGeneration

model = T5ForConditionalGeneration.from_pretrained('Unified_QA_2').to('cuda')

In [20]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("t5-small")

Downloading:   0%|          | 0.00/1.17k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/773k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/1.32M [00:00<?, ?B/s]

/usr/local/lib/python3.7/dist-packages/transformers/models/t5/tokenization_t5_fast.py:166: FutureWarning: This tokenizer was incorrectly instantiated with a model max length of 512 which will be corrected in Transformers v5.
For now, this behavior is kept to avoid breaking backwards compatibility when padding/encoding with `truncation is True`.
- Be aware that you SHOULD NOT rely on t5-small automatically truncating your input to 512 when padding/encoding.
- If you want to encode/pad to sequences longer than 512 you can either instantiate this tokenizer with `model_max_length` or pass `max_length` when encoding/padding.
- To avoid this warning, please instantiate this tokenizer with `model_max_length` set to your preferred value.
  FutureWarning,


In [38]:
def run_model(input_ids, **generator_args):
    global tokenizer
    res = model.generate(input_ids, **generator_args)
    return [tokenizer.decode(x) for x in res]

In [39]:
def predict(array_of_input_ids, options_list):
    '''
    This function takes list of string. Each string is a pair of question and 
    answers separated using \n(all lower cased). 
    For example: 
    which of the following is an example of a physical change? \n (a) lighting a match (b) breaking a glass (c) burning of gasoline (d) rusting of iron

    label_map = {'A':0,
                'B':1,
                'C':2,
                'D':3,
                'E':4,
                '1':0,
                '2':1,
                '3':2,
                '4':3,
                '5':4}

    This function will return predicted option. All answers are converted to 0, 1, 2, 3 and 4. 

    '''
    preds = [] # List to store all predicted labels.
        
    for i in range(len(array_of_input_ids)):

        # Converting input ids to torch tensor of Long type.
        input_ids = torch.from_numpy(array_of_input_ids[i]).type(torch.LongTensor).to('cuda')

        pred = run_model(input_ids.reshape((1,-1)))[0] #Reshaping because model takes input like (batch_size, sequence_length)

        #Pred is in the form like '<pad> answer </s>'. So we have to remove <pad> and </s>.
        pred = pred.replace('<pad>','')
        pred = pred.replace('</s>','')
        pred = pred.lstrip()

        options_list_i = options_list[i]

        label = None
        for j in range(len(options_list_i)):
            if pred in options_list_i[j]:
                label = j
        
        if label == None:
            label = random.randint(0,4)       

        preds.append(label)

    return preds

Easy

In [40]:
easy_train_preds = predict(easy_train_input_ids, df_easy_train['options_list'].values)

In [41]:
easy_dev_preds = predict(easy_dev_input_ids, df_easy_dev['options_list'].values)

In [42]:
easy_test_preds = predict(easy_test_input_ids, df_easy_test['options_list'].values)

In [43]:
a = accuracy_score(easy_train_labels, easy_train_preds)
print(f'Easy train accuracy is {a}')

b = accuracy_score(easy_dev_labels, easy_dev_preds)
print(f'Easy dev accuracy score is {b}')

c = accuracy_score(easy_test_labels, easy_test_preds)
print(f'Easy test accuracy score is {c}')

Easy train accuracy is 0.8973789426921368
Easy dev accuracy score is 0.47543859649122805
Easy test accuracy score is 0.4819023569023569


challenge

In [87]:
challenge_train_preds = predict(challenge_train_input_ids, df_challenge_train['options_list'].values)

In [88]:
challenge_dev_preds = predict(challenge_dev_input_ids, df_challenge_dev['options_list'].values)

In [89]:
challenge_test_preds = predict(challenge_test_input_ids, df_challenge_test['options_list'].values)

In [108]:
a = accuracy_score(challenge_train_labels,challenge_train_preds)
print(f'challenge train accuracy is {a}')

b = accuracy_score(challenge_dev_labels,challenge_dev_preds)
print(f'challenge dev accuracy score is {b}')

c = accuracy_score(challenge_test_labels, challenge_test_preds)
print(f'challenge test accuracy score is {c}')

challenge train accuracy is 0.6925826630920465
challenge dev accuracy score is 0.3377926421404682
challenge test accuracy score is 0.32764505119453924


## Reference Links:
https://github.com/sobamchan/race-bert/blob/master/race.py

https://medium.com/analytics-vidhya/multiple-choice-qa-using-deep-learning-44689618a253